In [1]:
import igraph as ig#version 0.10.4 returned Node with 17916 
import cairo
import pandas as pd
import matplotlib.pyplot as plt
pd.set_option('display.float_format', lambda x: '%.3f' % x)

## 0.0 Load Data

In [2]:
df_bene = pd.read_csv('Train_Beneficiarydata-1542865627584.csv')
df_inp = pd.read_csv('Train_Inpatientdata-1542865627584.csv')
df_outp = pd.read_csv('Train_Outpatientdata-1542865627584.csv')
df_label = pd.read_csv('Train-1542865627584.csv')
df_inp.head()

BeneID   ClaimID ClaimStartDt  ClaimEndDt  Provider  \
0  BENE11001  CLM46614   2009-04-12  2009-04-18  PRV55912   
1  BENE11001  CLM66048   2009-08-31  2009-09-02  PRV55907   
2  BENE11001  CLM68358   2009-09-17  2009-09-20  PRV56046   
3  BENE11011  CLM38412   2009-02-14  2009-02-22  PRV52405   
4  BENE11014  CLM63689   2009-08-13  2009-08-30  PRV56614   

   InscClaimAmtReimbursed AttendingPhysician OperatingPhysician  \
0                   26000          PHY390922                NaN   
1                    5000          PHY318495          PHY318495   
2                    5000          PHY372395                NaN   
3                    5000          PHY369659          PHY392961   
4                   10000          PHY379376          PHY398258   

  OtherPhysician AdmissionDt  ... ClmDiagnosisCode_7  ClmDiagnosisCode_8  \
0            NaN  2009-04-12  ...               2724               19889   
1            NaN  2009-08-31  ...                NaN                 NaN   
2      PHY324689  2009-09-17  ...                NaN                 NaN   
3      PHY349768  2009-02-14  ...              25062               40390   
4            NaN  2009-08-13  ...               5119               29620   

  ClmDiagnosisCode_9 ClmDiagnosisCode_10 ClmProcedureCode_1  \
0               5849                 NaN                NaN   
1                NaN                 NaN           7092.000   
2                NaN                 NaN                NaN   
3               4019                 NaN            331.000   
4              20300                 NaN           3893.000   

  ClmProcedureCode_2 ClmProcedureCode_3 ClmProcedureCode_4 ClmProcedureCode_5  \
0                NaN                NaN                NaN                NaN   
1                NaN                NaN                NaN                NaN   
2                NaN                NaN                NaN                NaN   
3                NaN                NaN                NaN                NaN   
4                NaN                NaN                NaN                NaN   

  ClmProcedureCode_6  
0                NaN  
1                NaN  
2                NaN  
3                NaN  
4                NaN  

[5 rows x 30 columns]

## 1 Data Parsing

### 1.1 Data Column Selection

In [3]:
df_inp = df_inp[['BeneID','Provider','InscClaimAmtReimbursed','AttendingPhysician','OperatingPhysician','OtherPhysician',
                 'ClmDiagnosisCode_1','ClmDiagnosisCode_2','ClmDiagnosisCode_3','ClmDiagnosisCode_4','ClmDiagnosisCode_5',
                 'ClmDiagnosisCode_6','ClmDiagnosisCode_7','ClmDiagnosisCode_8','ClmDiagnosisCode_9','ClmDiagnosisCode_10',
                 'ClmProcedureCode_1','ClmProcedureCode_2','ClmProcedureCode_3','ClmProcedureCode_4','ClmProcedureCode_5',
                 'ClmProcedureCode_6']]
df_inp['InOut'] = 'In'
df_inp.head()

BeneID  Provider  InscClaimAmtReimbursed AttendingPhysician  \
0  BENE11001  PRV55912                   26000          PHY390922   
1  BENE11001  PRV55907                    5000          PHY318495   
2  BENE11001  PRV56046                    5000          PHY372395   
3  BENE11011  PRV52405                    5000          PHY369659   
4  BENE11014  PRV56614                   10000          PHY379376   

  OperatingPhysician OtherPhysician ClmDiagnosisCode_1 ClmDiagnosisCode_2  \
0                NaN            NaN               1970               4019   
1          PHY318495            NaN               6186               2948   
2                NaN      PHY324689              29623              30390   
3          PHY392961      PHY349768              43491               2762   
4          PHY398258            NaN                042               3051   

  ClmDiagnosisCode_3 ClmDiagnosisCode_4  ... ClmDiagnosisCode_8  \
0               5853               7843  ...              19889   
1              56400                NaN  ...                NaN   
2              71690              34590  ...                NaN   
3               7843              32723  ...              40390   
4              34400               5856  ...              29620   

  ClmDiagnosisCode_9 ClmDiagnosisCode_10 ClmProcedureCode_1  \
0               5849                 NaN                NaN   
1                NaN                 NaN           7092.000   
2                NaN                 NaN                NaN   
3               4019                 NaN            331.000   
4              20300                 NaN           3893.000   

  ClmProcedureCode_2 ClmProcedureCode_3  ClmProcedureCode_4  \
0                NaN                NaN                 NaN   
1                NaN                NaN                 NaN   
2                NaN                NaN                 NaN   
3                NaN                NaN                 NaN   
4                NaN                NaN                 NaN   

   ClmProcedureCode_5  ClmProcedureCode_6  InOut  
0                 NaN                 NaN     In  
1                 NaN                 NaN     In  
2                 NaN                 NaN     In  
3                 NaN                 NaN     In  
4                 NaN                 NaN     In  

[5 rows x 23 columns]

In [4]:
df_outp = df_outp[['BeneID','Provider','InscClaimAmtReimbursed','AttendingPhysician','OperatingPhysician','OtherPhysician',
                 'ClmDiagnosisCode_1','ClmDiagnosisCode_2','ClmDiagnosisCode_3','ClmDiagnosisCode_4','ClmDiagnosisCode_5',
                 'ClmDiagnosisCode_6','ClmDiagnosisCode_7','ClmDiagnosisCode_8','ClmDiagnosisCode_9','ClmDiagnosisCode_10',
                 'ClmProcedureCode_1','ClmProcedureCode_2','ClmProcedureCode_3','ClmProcedureCode_4','ClmProcedureCode_5',
                 'ClmProcedureCode_6']]
df_outp['InOut'] = 'Out'
df_outp.head()

BeneID  Provider  InscClaimAmtReimbursed AttendingPhysician  \
0  BENE11002  PRV56011                      30          PHY326117   
1  BENE11003  PRV57610                      80          PHY362868   
2  BENE11003  PRV57595                      10          PHY328821   
3  BENE11004  PRV56011                      40          PHY334319   
4  BENE11004  PRV56011                     200          PHY403831   

  OperatingPhysician OtherPhysician ClmDiagnosisCode_1 ClmDiagnosisCode_2  \
0                NaN            NaN              78943              V5866   
1                NaN            NaN               6115                NaN   
2                NaN            NaN               2723                NaN   
3                NaN            NaN              71988                NaN   
4                NaN            NaN              82382              30000   

  ClmDiagnosisCode_3 ClmDiagnosisCode_4  ... ClmDiagnosisCode_8  \
0              V1272                NaN  ...                NaN   
1                NaN                NaN  ...                NaN   
2                NaN                NaN  ...                NaN   
3                NaN                NaN  ...                NaN   
4              72887               4280  ...                NaN   

  ClmDiagnosisCode_9 ClmDiagnosisCode_10 ClmProcedureCode_1  \
0                NaN                 NaN                NaN   
1                NaN                 NaN                NaN   
2                NaN                 NaN                NaN   
3                NaN                 NaN                NaN   
4                NaN                 NaN                NaN   

  ClmProcedureCode_2 ClmProcedureCode_3  ClmProcedureCode_4  \
0                NaN                NaN                 NaN   
1                NaN                NaN                 NaN   
2                NaN                NaN                 NaN   
3                NaN                NaN                 NaN   
4                NaN                NaN                 NaN   

   ClmProcedureCode_5  ClmProcedureCode_6  InOut  
0                 NaN                 NaN    Out  
1                 NaN                 NaN    Out  
2                 NaN                 NaN    Out  
3                 NaN                 NaN    Out  
4                 NaN                 NaN    Out  

[5 rows x 23 columns]

### 1.2 Union Both File

In [5]:
df = pd.concat([df_inp, df_outp], ignore_index=True)
df.head()

BeneID  Provider  InscClaimAmtReimbursed AttendingPhysician  \
0  BENE11001  PRV55912                   26000          PHY390922   
1  BENE11001  PRV55907                    5000          PHY318495   
2  BENE11001  PRV56046                    5000          PHY372395   
3  BENE11011  PRV52405                    5000          PHY369659   
4  BENE11014  PRV56614                   10000          PHY379376   

  OperatingPhysician OtherPhysician ClmDiagnosisCode_1 ClmDiagnosisCode_2  \
0                NaN            NaN               1970               4019   
1          PHY318495            NaN               6186               2948   
2                NaN      PHY324689              29623              30390   
3          PHY392961      PHY349768              43491               2762   
4          PHY398258            NaN                042               3051   

  ClmDiagnosisCode_3 ClmDiagnosisCode_4  ... ClmDiagnosisCode_8  \
0               5853               7843  ...              19889   
1              56400                NaN  ...                NaN   
2              71690              34590  ...                NaN   
3               7843              32723  ...              40390   
4              34400               5856  ...              29620   

  ClmDiagnosisCode_9 ClmDiagnosisCode_10 ClmProcedureCode_1  \
0               5849                 NaN                NaN   
1                NaN                 NaN           7092.000   
2                NaN                 NaN                NaN   
3               4019                 NaN            331.000   
4              20300                 NaN           3893.000   

  ClmProcedureCode_2 ClmProcedureCode_3  ClmProcedureCode_4  \
0                NaN                NaN                 NaN   
1                NaN                NaN                 NaN   
2                NaN                NaN                 NaN   
3                NaN                NaN                 NaN   
4                NaN                NaN                 NaN   

   ClmProcedureCode_5  ClmProcedureCode_6  InOut  
0                 NaN                 NaN     In  
1                 NaN                 NaN     In  
2                 NaN                 NaN     In  
3                 NaN                 NaN     In  
4                 NaN                 NaN     In  

[5 rows x 23 columns]

### 1.3 Beneficiary, Provider, and Physician analysis

In [6]:
print('Total rows of data: ', len(df))
print('Total unique beneficiary in data: ', len(df.BeneID.unique()))
print('Total unique provider in data: ', len(df.Provider.unique()))
print('Total unique attending physician in data: ', len(df.AttendingPhysician.unique()))
print('Total unique beneficiary in source: ', len(df_bene.BeneID.unique()))
print('Total unique provider in source: ', len(df_label.Provider.unique()))

Total rows of data:  558211
Total unique beneficiary in data:  138556
Total unique provider in data:  5410
Total unique attending physician in data:  82064
Total unique beneficiary in source:  138556
Total unique provider in source:  5410


#### 1.3.1 Beneficiary going to multiple Provider

In [7]:
distinct_benepro = df[['BeneID','Provider','InscClaimAmtReimbursed']].groupby(['BeneID','Provider']).count().reset_index()[['BeneID','Provider']]
distinct_bene = distinct_benepro.groupby('BeneID').count().reset_index()
print(len(distinct_bene.loc[distinct_bene.Provider > 1]), 'beneficiary out of', len(df.BeneID.unique()),'(',round(len(distinct_bene.loc[distinct_bene.Provider > 1])/len(df.BeneID.unique())*100,2),'% ) attend more than 1 provider')

91653 beneficiary out of 138556 ( 66.15 % ) attend more than 1 provider


#### 1.3.2 Provider taking care of multiple Beneficiary

In [8]:
distinct_pro = distinct_benepro.groupby('Provider').count().reset_index()
print(len(distinct_pro.loc[distinct_pro.BeneID > 1]), 'provider out of', len(df_label.Provider.unique()),'(',round(len(distinct_pro.loc[distinct_pro.BeneID > 1])/len(df_label.Provider.unique())*100,2),'% ) take care of more than 1 beneficiary')

5157 provider out of 5410 ( 95.32 % ) take care of more than 1 beneficiary


#### 1.3.3 Provider with more than 1 Attending Physician

In [9]:
distinct_prophy = df[['Provider','AttendingPhysician','InscClaimAmtReimbursed']].groupby(['Provider','AttendingPhysician']).count().reset_index()[['Provider','AttendingPhysician']]
distinct_prop = distinct_prophy.groupby('Provider').count().reset_index()
print(len(distinct_prop.loc[distinct_prop.AttendingPhysician > 1]), 'provider out of', len(df.Provider.unique()),'(',round(len(distinct_prop.loc[distinct_prop.AttendingPhysician > 1])/len(df.Provider.unique())*100,2),'% ) have more than 1 attending physician')

4420 provider out of 5410 ( 81.7 % ) have more than 1 attending physician


#### 1.3.4 Attending Physician work for more than 1 Provider

In [10]:
distinct_phy = distinct_prophy.groupby('AttendingPhysician').count().reset_index()
print(len(distinct_phy.loc[distinct_phy.Provider > 1]), 'attending physician out of', len(df.AttendingPhysician.unique()),'(',round(len(distinct_phy.loc[distinct_phy.Provider > 1])/len(df.AttendingPhysician.unique())*100,2),'% ) go to more than 1 provider')

5219 attending physician out of 82064 ( 6.36 % ) go to more than 1 provider


### 1.4 Column Combination

In [11]:
df.head()

BeneID  Provider  InscClaimAmtReimbursed AttendingPhysician  \
0  BENE11001  PRV55912                   26000          PHY390922   
1  BENE11001  PRV55907                    5000          PHY318495   
2  BENE11001  PRV56046                    5000          PHY372395   
3  BENE11011  PRV52405                    5000          PHY369659   
4  BENE11014  PRV56614                   10000          PHY379376   

  OperatingPhysician OtherPhysician ClmDiagnosisCode_1 ClmDiagnosisCode_2  \
0                NaN            NaN               1970               4019   
1          PHY318495            NaN               6186               2948   
2                NaN      PHY324689              29623              30390   
3          PHY392961      PHY349768              43491               2762   
4          PHY398258            NaN                042               3051   

  ClmDiagnosisCode_3 ClmDiagnosisCode_4  ... ClmDiagnosisCode_8  \
0               5853               7843  ...              19889   
1              56400                NaN  ...                NaN   
2              71690              34590  ...                NaN   
3               7843              32723  ...              40390   
4              34400               5856  ...              29620   

  ClmDiagnosisCode_9 ClmDiagnosisCode_10 ClmProcedureCode_1  \
0               5849                 NaN                NaN   
1                NaN                 NaN           7092.000   
2                NaN                 NaN                NaN   
3               4019                 NaN            331.000   
4              20300                 NaN           3893.000   

  ClmProcedureCode_2 ClmProcedureCode_3  ClmProcedureCode_4  \
0                NaN                NaN                 NaN   
1                NaN                NaN                 NaN   
2                NaN                NaN                 NaN   
3                NaN                NaN                 NaN   
4                NaN                NaN                 NaN   

   ClmProcedureCode_5  ClmProcedureCode_6  InOut  
0                 NaN                 NaN     In  
1                 NaN                 NaN     In  
2                 NaN                 NaN     In  
3                 NaN                 NaN     In  
4                 NaN                 NaN     In  

[5 rows x 23 columns]

In [12]:
def if_na(column_value):
    if column_value.isna():
        return 0
    return 1

In [13]:
df['NumberOfPhysician'] = df['AttendingPhysician'].notna().astype(int) + df['OperatingPhysician'].notna().astype(int) + df['OtherPhysician'].notna().astype(int)

In [14]:
df['ClmDiagnosisCode_Count'] = (df['ClmDiagnosisCode_1'].notna().astype(int) + df['ClmDiagnosisCode_2'].notna().astype(int)
             + df['ClmDiagnosisCode_3'].notna().astype(int) + df['ClmDiagnosisCode_4'].notna().astype(int)
             + df['ClmDiagnosisCode_5'].notna().astype(int) + df['ClmDiagnosisCode_6'].notna().astype(int)
             + df['ClmDiagnosisCode_7'].notna().astype(int) + df['ClmDiagnosisCode_8'].notna().astype(int)
             + df['ClmDiagnosisCode_9'].notna().astype(int) + df['ClmDiagnosisCode_10'].notna().astype(int))

In [15]:
df['ClmProcedureCode_Count'] = (df['ClmProcedureCode_1'].notna().astype(int) + df['ClmProcedureCode_2'].notna().astype(int)
             + df['ClmProcedureCode_3'].notna().astype(int) + df['ClmProcedureCode_4'].notna().astype(int)
             + df['ClmProcedureCode_5'].notna().astype(int) + df['ClmProcedureCode_6'].notna().astype(int))

In [16]:
df = df[['BeneID','Provider','InscClaimAmtReimbursed','AttendingPhysician','NumberOfPhysician','ClmDiagnosisCode_Count','ClmProcedureCode_Count','InOut']]
df

BeneID  Provider  InscClaimAmtReimbursed AttendingPhysician  \
0        BENE11001  PRV55912                   26000          PHY390922   
1        BENE11001  PRV55907                    5000          PHY318495   
2        BENE11001  PRV56046                    5000          PHY372395   
3        BENE11011  PRV52405                    5000          PHY369659   
4        BENE11014  PRV56614                   10000          PHY379376   
...            ...       ...                     ...                ...   
558206  BENE159198  PRV53699                     800          PHY364188   
558207  BENE159198  PRV53702                     400          PHY423019   
558208  BENE159198  PRV53676                      60          PHY361063   
558209  BENE159198  PRV53689                      70          PHY403198   
558210  BENE159198  PRV53689                      80          PHY419379   

        NumberOfPhysician  ClmDiagnosisCode_Count  ClmProcedureCode_Count  \
0                       1                       9                       0   
1                       2                       3                       1   
2                       2                       6                       0   
3                       3                       9                       1   
4                       2                       9                       1   
...                   ...                     ...                     ...   
558206                  3                       3                       0   
558207                  2                       3                       0   
558208                  1                       2                       0   
558209                  2                       0                       0   
558210                  2                       8                       0   

       InOut  
0         In  
1         In  
2         In  
3         In  
4         In  
...      ...  
558206   Out  
558207   Out  
558208   Out  
558209   Out  
558210   Out  

[558211 rows x 8 columns]

### 1.5 Create Edge File

In [17]:
df_inp = df.loc[df.InOut == 'In']
df_out = df.loc[df.InOut == 'Out']

In [18]:
#Using Beneficiary as Edge for Provider
graph_net_inp_count = {}
count = 0
total = len(df_bene)

for bene in df_bene.BeneID:
    count += 1
    print(round(count / total * 100,2), '%')
    sub_net = df_inp.loc[df_inp.BeneID == bene].sort_values(by='Provider').reset_index(drop=True)
    sub_net_p = sub_net.Provider
    sub_net_reimburse = round(sub_net.InscClaimAmtReimbursed.mean(),2)
    sub_net_phy = round(sub_net.NumberOfPhysician.mean(),2)
    sub_net_diag = round(sub_net.ClmDiagnosisCode_Count.mean(),2)
    sub_net_proce = round(sub_net.ClmProcedureCode_Count.mean(),2)
    pair_len = len(sub_net)
    if pair_len > 2:
        for providerx in range(pair_len):
            for providery in range(providerx+1,pair_len):
                if (sub_net_p[providerx],sub_net_p[providery]) in graph_net_inp_count:
                    graph_net_inp_count[(sub_net_p[providerx],sub_net_p[providery])][0] += 1
                    graph_net_inp_count[(sub_net_p[providerx],sub_net_p[providery])][1] += sub_net_reimburse
                    graph_net_inp_count[(sub_net_p[providerx],sub_net_p[providery])][2] += sub_net_phy
                    graph_net_inp_count[(sub_net_p[providerx],sub_net_p[providery])][3] += sub_net_diag
                    graph_net_inp_count[(sub_net_p[providerx],sub_net_p[providery])][4] += sub_net_proce
                else:
                    graph_net_inp_count[(sub_net_p[providerx],sub_net_p[providery])] = []
                    graph_net_inp_count[(sub_net_p[providerx],sub_net_p[providery])].append(1)
                    graph_net_inp_count[(sub_net_p[providerx],sub_net_p[providery])].append(sub_net_reimburse)
                    graph_net_inp_count[(sub_net_p[providerx],sub_net_p[providery])].append(sub_net_phy)
                    graph_net_inp_count[(sub_net_p[providerx],sub_net_p[providery])].append(sub_net_diag)
                    graph_net_inp_count[(sub_net_p[providerx],sub_net_p[providery])].append(sub_net_proce)
    elif pair_len == 2:
        p_from = sub_net.Provider[0]
        p_to = sub_net.Provider[1]
        if (p_from,p_to) in graph_net_inp_count:
            graph_net_inp_count[(p_from,p_to)][0] += 1
            graph_net_inp_count[(p_from,p_to)][1] += sub_net_reimburse
            graph_net_inp_count[(p_from,p_to)][2] += sub_net_phy
            graph_net_inp_count[(p_from,p_to)][3] += sub_net_diag
            graph_net_inp_count[(p_from,p_to)][4] += sub_net_proce
        else:
            graph_net_inp_count[(p_from,p_to)] = []
            graph_net_inp_count[(p_from,p_to)].append(1)
            graph_net_inp_count[(p_from,p_to)].append(sub_net_reimburse)
            graph_net_inp_count[(p_from,p_to)].append(sub_net_phy)
            graph_net_inp_count[(p_from,p_to)].append(sub_net_diag)
            graph_net_inp_count[(p_from,p_to)].append(sub_net_proce)
    else:
        pass
graph_net_inp_count

0.0 %
0.0 %
0.0 %
0.0 %
0.0 %
0.0 %
0.01 %
0.01 %
0.01 %
0.01 %
0.01 %
0.01 %
0.01 %
0.01 %
0.01 %
0.01 %
0.01 %
0.01 %
0.01 %
0.01 %
0.02 %
0.02 %
0.02 %
0.02 %
0.02 %
0.02 %
0.02 %
0.02 %
0.02 %
0.02 %
0.02 %
0.02 %
0.02 %
0.02 %
0.03 %
0.03 %
0.03 %
0.03 %
0.03 %
0.03 %
0.03 %
0.03 %
0.03 %
0.03 %
0.03 %
0.03 %
0.03 %
0.03 %
0.04 %
0.04 %
0.04 %
0.04 %
0.04 %
0.04 %
0.04 %
0.04 %
0.04 %
0.04 %
0.04 %
0.04 %
0.04 %
0.04 %
0.05 %
0.05 %
0.05 %
0.05 %
0.05 %
0.05 %
0.05 %
0.05 %
0.05 %
0.05 %
0.05 %
0.05 %
0.05 %
0.05 %
0.06 %
0.06 %
0.06 %
0.06 %
0.06 %
0.06 %
0.06 %
0.06 %
0.06 %
0.06 %
0.06 %
0.06 %
0.06 %
0.06 %
0.07 %
0.07 %
0.07 %
0.07 %
0.07 %
0.07 %
0.07 %
0.07 %
0.07 %
0.07 %
0.07 %
0.07 %
0.07 %
0.08 %
0.08 %
0.08 %
0.08 %
0.08 %
0.08 %
0.08 %
0.08 %
0.08 %
0.08 %
0.08 %
0.08 %
0.08 %
0.08 %
0.09 %
0.09 %
0.09 %
0.09 %
0.09 %
0.09 %
0.09 %
0.09 %
0.09 %
0.09 %
0.09 %
0.09 %
0.09 %
0.09 %
0.1 %
0.1 %
0.1 %
0.1 %
0.1 %
0.1 %
0.1 %
0.1 %
0.1 %
0.1 %
0.1 %
0.1 %
0.1 %
0.1 %
0.11 

0.9 %
0.9 %
0.9 %
0.9 %
0.9 %
0.9 %
0.9 %
0.9 %
0.9 %
0.9 %
0.9 %
0.9 %
0.91 %
0.91 %
0.91 %
0.91 %
0.91 %
0.91 %
0.91 %
0.91 %
0.91 %
0.91 %
0.91 %
0.91 %
0.91 %
0.91 %
0.92 %
0.92 %
0.92 %
0.92 %
0.92 %
0.92 %
0.92 %
0.92 %
0.92 %
0.92 %
0.92 %
0.92 %
0.92 %
0.92 %
0.93 %
0.93 %
0.93 %
0.93 %
0.93 %
0.93 %
0.93 %
0.93 %
0.93 %
0.93 %
0.93 %
0.93 %
0.93 %
0.93 %
0.94 %
0.94 %
0.94 %
0.94 %
0.94 %
0.94 %
0.94 %
0.94 %
0.94 %
0.94 %
0.94 %
0.94 %
0.94 %
0.94 %
0.95 %
0.95 %
0.95 %
0.95 %
0.95 %
0.95 %
0.95 %
0.95 %
0.95 %
0.95 %
0.95 %
0.95 %
0.95 %
0.95 %
0.96 %
0.96 %
0.96 %
0.96 %
0.96 %
0.96 %
0.96 %
0.96 %
0.96 %
0.96 %
0.96 %
0.96 %
0.96 %
0.96 %
0.97 %
0.97 %
0.97 %
0.97 %
0.97 %
0.97 %
0.97 %
0.97 %
0.97 %
0.97 %
0.97 %
0.97 %
0.97 %
0.98 %
0.98 %
0.98 %
0.98 %
0.98 %
0.98 %
0.98 %
0.98 %
0.98 %
0.98 %
0.98 %
0.98 %
0.98 %
0.98 %
0.99 %
0.99 %
0.99 %
0.99 %
0.99 %
0.99 %
0.99 %
0.99 %
0.99 %
0.99 %
0.99 %
0.99 %
0.99 %
0.99 %
1.0 %
1.0 %
1.0 %
1.0 %
1.0 %
1.0 %
1.0 %
1.0 %
1.0 %

1.77 %
1.77 %
1.77 %
1.77 %
1.77 %
1.77 %
1.77 %
1.77 %
1.77 %
1.77 %
1.77 %
1.77 %
1.77 %
1.77 %
1.78 %
1.78 %
1.78 %
1.78 %
1.78 %
1.78 %
1.78 %
1.78 %
1.78 %
1.78 %
1.78 %
1.78 %
1.78 %
1.78 %
1.79 %
1.79 %
1.79 %
1.79 %
1.79 %
1.79 %
1.79 %
1.79 %
1.79 %
1.79 %
1.79 %
1.79 %
1.79 %
1.79 %
1.8 %
1.8 %
1.8 %
1.8 %
1.8 %
1.8 %
1.8 %
1.8 %
1.8 %
1.8 %
1.8 %
1.8 %
1.8 %
1.81 %
1.81 %
1.81 %
1.81 %
1.81 %
1.81 %
1.81 %
1.81 %
1.81 %
1.81 %
1.81 %
1.81 %
1.81 %
1.81 %
1.82 %
1.82 %
1.82 %
1.82 %
1.82 %
1.82 %
1.82 %
1.82 %
1.82 %
1.82 %
1.82 %
1.82 %
1.82 %
1.82 %
1.83 %
1.83 %
1.83 %
1.83 %
1.83 %
1.83 %
1.83 %
1.83 %
1.83 %
1.83 %
1.83 %
1.83 %
1.83 %
1.83 %
1.84 %
1.84 %
1.84 %
1.84 %
1.84 %
1.84 %
1.84 %
1.84 %
1.84 %
1.84 %
1.84 %
1.84 %
1.84 %
1.84 %
1.85 %
1.85 %
1.85 %
1.85 %
1.85 %
1.85 %
1.85 %
1.85 %
1.85 %
1.85 %
1.85 %
1.85 %
1.85 %
1.85 %
1.86 %
1.86 %
1.86 %
1.86 %
1.86 %
1.86 %
1.86 %
1.86 %
1.86 %
1.86 %
1.86 %
1.86 %
1.86 %
1.86 %
1.87 %
1.87 %
1.87 %
1.87 %
1.87 %
1.87 

2.66 %
2.66 %
2.66 %
2.66 %
2.66 %
2.66 %
2.66 %
2.66 %
2.66 %
2.66 %
2.66 %
2.66 %
2.66 %
2.67 %
2.67 %
2.67 %
2.67 %
2.67 %
2.67 %
2.67 %
2.67 %
2.67 %
2.67 %
2.67 %
2.67 %
2.67 %
2.67 %
2.68 %
2.68 %
2.68 %
2.68 %
2.68 %
2.68 %
2.68 %
2.68 %
2.68 %
2.68 %
2.68 %
2.68 %
2.68 %
2.68 %
2.69 %
2.69 %
2.69 %
2.69 %
2.69 %
2.69 %
2.69 %
2.69 %
2.69 %
2.69 %
2.69 %
2.69 %
2.69 %
2.69 %
2.7 %
2.7 %
2.7 %
2.7 %
2.7 %
2.7 %
2.7 %
2.7 %
2.7 %
2.7 %
2.7 %
2.7 %
2.7 %
2.71 %
2.71 %
2.71 %
2.71 %
2.71 %
2.71 %
2.71 %
2.71 %
2.71 %
2.71 %
2.71 %
2.71 %
2.71 %
2.71 %
2.72 %
2.72 %
2.72 %
2.72 %
2.72 %
2.72 %
2.72 %
2.72 %
2.72 %
2.72 %
2.72 %
2.72 %
2.72 %
2.72 %
2.73 %
2.73 %
2.73 %
2.73 %
2.73 %
2.73 %
2.73 %
2.73 %
2.73 %
2.73 %
2.73 %
2.73 %
2.73 %
2.73 %
2.74 %
2.74 %
2.74 %
2.74 %
2.74 %
2.74 %
2.74 %
2.74 %
2.74 %
2.74 %
2.74 %
2.74 %
2.74 %
2.74 %
2.75 %
2.75 %
2.75 %
2.75 %
2.75 %
2.75 %
2.75 %
2.75 %
2.75 %
2.75 %
2.75 %
2.75 %
2.75 %
2.75 %
2.76 %
2.76 %
2.76 %
2.76 %
2.76 %
2.76 %
2.76 

3.51 %
3.52 %
3.52 %
3.52 %
3.52 %
3.52 %
3.52 %
3.52 %
3.52 %
3.52 %
3.52 %
3.52 %
3.52 %
3.52 %
3.52 %
3.53 %
3.53 %
3.53 %
3.53 %
3.53 %
3.53 %
3.53 %
3.53 %
3.53 %
3.53 %
3.53 %
3.53 %
3.53 %
3.54 %
3.54 %
3.54 %
3.54 %
3.54 %
3.54 %
3.54 %
3.54 %
3.54 %
3.54 %
3.54 %
3.54 %
3.54 %
3.54 %
3.55 %
3.55 %
3.55 %
3.55 %
3.55 %
3.55 %
3.55 %
3.55 %
3.55 %
3.55 %
3.55 %
3.55 %
3.55 %
3.55 %
3.56 %
3.56 %
3.56 %
3.56 %
3.56 %
3.56 %
3.56 %
3.56 %
3.56 %
3.56 %
3.56 %
3.56 %
3.56 %
3.56 %
3.57 %
3.57 %
3.57 %
3.57 %
3.57 %
3.57 %
3.57 %
3.57 %
3.57 %
3.57 %
3.57 %
3.57 %
3.57 %
3.57 %
3.58 %
3.58 %
3.58 %
3.58 %
3.58 %
3.58 %
3.58 %
3.58 %
3.58 %
3.58 %
3.58 %
3.58 %
3.58 %
3.58 %
3.59 %
3.59 %
3.59 %
3.59 %
3.59 %
3.59 %
3.59 %
3.59 %
3.59 %
3.59 %
3.59 %
3.59 %
3.59 %
3.59 %
3.6 %
3.6 %
3.6 %
3.6 %
3.6 %
3.6 %
3.6 %
3.6 %
3.6 %
3.6 %
3.6 %
3.6 %
3.6 %
3.61 %
3.61 %
3.61 %
3.61 %
3.61 %
3.61 %
3.61 %
3.61 %
3.61 %
3.61 %
3.61 %
3.61 %
3.61 %
3.61 %
3.62 %
3.62 %
3.62 %
3.62 %
3.62 %
3.62 

...

96.98 %
96.98 %
96.98 %
96.98 %
96.98 %
96.98 %
96.99 %
96.99 %
96.99 %
96.99 %
96.99 %
96.99 %
96.99 %
96.99 %
96.99 %
96.99 %
96.99 %
96.99 %
96.99 %
96.99 %
97.0 %
97.0 %
97.0 %
97.0 %
97.0 %
97.0 %
97.0 %
97.0 %
97.0 %
97.0 %
97.0 %
97.0 %
97.0 %
97.0 %
97.01 %
97.01 %
97.01 %
97.01 %
97.01 %
97.01 %
97.01 %
97.01 %
97.01 %
97.01 %
97.01 %
97.01 %
97.01 %
97.01 %
97.02 %
97.02 %
97.02 %
97.02 %
97.02 %
97.02 %
97.02 %
97.02 %
97.02 %
97.02 %
97.02 %
97.02 %
97.02 %
97.03 %
97.03 %
97.03 %
97.03 %
97.03 %
97.03 %
97.03 %
97.03 %
97.03 %
97.03 %
97.03 %
97.03 %
97.03 %
97.03 %
97.04 %
97.04 %
97.04 %
97.04 %
97.04 %
97.04 %
97.04 %
97.04 %
97.04 %
97.04 %
97.04 %
97.04 %
97.04 %
97.04 %
97.05 %
97.05 %
97.05 %
97.05 %
97.05 %
97.05 %
97.05 %
97.05 %
97.05 %
97.05 %
97.05 %
97.05 %
97.05 %
97.05 %
97.06 %
97.06 %
97.06 %
97.06 %
97.06 %
97.06 %
97.06 %
97.06 %
97.06 %
97.06 %
97.06 %
97.06 %
97.06 %
97.06 %
97.07 %
97.07 %
97.07 %
97.07 %
97.07 %
97.07 %
97.07 %
97.07 %
97.07 %
97.07 

97.76 %
97.76 %
97.77 %
97.77 %
97.77 %
97.77 %
97.77 %
97.77 %
97.77 %
97.77 %
97.77 %
97.77 %
97.77 %
97.77 %
97.77 %
97.77 %
97.78 %
97.78 %
97.78 %
97.78 %
97.78 %
97.78 %
97.78 %
97.78 %
97.78 %
97.78 %
97.78 %
97.78 %
97.78 %
97.79 %
97.79 %
97.79 %
97.79 %
97.79 %
97.79 %
97.79 %
97.79 %
97.79 %
97.79 %
97.79 %
97.79 %
97.79 %
97.79 %
97.8 %
97.8 %
97.8 %
97.8 %
97.8 %
97.8 %
97.8 %
97.8 %
97.8 %
97.8 %
97.8 %
97.8 %
97.8 %
97.8 %
97.81 %
97.81 %
97.81 %
97.81 %
97.81 %
97.81 %
97.81 %
97.81 %
97.81 %
97.81 %
97.81 %
97.81 %
97.81 %
97.81 %
97.82 %
97.82 %
97.82 %
97.82 %
97.82 %
97.82 %
97.82 %
97.82 %
97.82 %
97.82 %
97.82 %
97.82 %
97.82 %
97.82 %
97.83 %
97.83 %
97.83 %
97.83 %
97.83 %
97.83 %
97.83 %
97.83 %
97.83 %
97.83 %
97.83 %
97.83 %
97.83 %
97.83 %
97.84 %
97.84 %
97.84 %
97.84 %
97.84 %
97.84 %
97.84 %
97.84 %
97.84 %
97.84 %
97.84 %
97.84 %
97.84 %
97.84 %
97.85 %
97.85 %
97.85 %
97.85 %
97.85 %
97.85 %
97.85 %
97.85 %
97.85 %
97.85 %
97.85 %
97.85 %
97.85 %
97.86 

98.54 %
98.54 %
98.54 %
98.54 %
98.54 %
98.54 %
98.54 %
98.54 %
98.54 %
98.54 %
98.55 %
98.55 %
98.55 %
98.55 %
98.55 %
98.55 %
98.55 %
98.55 %
98.55 %
98.55 %
98.55 %
98.55 %
98.55 %
98.56 %
98.56 %
98.56 %
98.56 %
98.56 %
98.56 %
98.56 %
98.56 %
98.56 %
98.56 %
98.56 %
98.56 %
98.56 %
98.56 %
98.57 %
98.57 %
98.57 %
98.57 %
98.57 %
98.57 %
98.57 %
98.57 %
98.57 %
98.57 %
98.57 %
98.57 %
98.57 %
98.57 %
98.58 %
98.58 %
98.58 %
98.58 %
98.58 %
98.58 %
98.58 %
98.58 %
98.58 %
98.58 %
98.58 %
98.58 %
98.58 %
98.58 %
98.59 %
98.59 %
98.59 %
98.59 %
98.59 %
98.59 %
98.59 %
98.59 %
98.59 %
98.59 %
98.59 %
98.59 %
98.59 %
98.59 %
98.6 %
98.6 %
98.6 %
98.6 %
98.6 %
98.6 %
98.6 %
98.6 %
98.6 %
98.6 %
98.6 %
98.6 %
98.6 %
98.6 %
98.61 %
98.61 %
98.61 %
98.61 %
98.61 %
98.61 %
98.61 %
98.61 %
98.61 %
98.61 %
98.61 %
98.61 %
98.61 %
98.62 %
98.62 %
98.62 %
98.62 %
98.62 %
98.62 %
98.62 %
98.62 %
98.62 %
98.62 %
98.62 %
98.62 %
98.62 %
98.62 %
98.63 %
98.63 %
98.63 %
98.63 %
98.63 %
98.63 %
98.63 

99.3 %
99.3 %
99.31 %
99.31 %
99.31 %
99.31 %
99.31 %
99.31 %
99.31 %
99.31 %
99.31 %
99.31 %
99.31 %
99.31 %
99.31 %
99.32 %
99.32 %
99.32 %
99.32 %
99.32 %
99.32 %
99.32 %
99.32 %
99.32 %
99.32 %
99.32 %
99.32 %
99.32 %
99.32 %
99.33 %
99.33 %
99.33 %
99.33 %
99.33 %
99.33 %
99.33 %
99.33 %
99.33 %
99.33 %
99.33 %
99.33 %
99.33 %
99.33 %
99.34 %
99.34 %
99.34 %
99.34 %
99.34 %
99.34 %
99.34 %
99.34 %
99.34 %
99.34 %
99.34 %
99.34 %
99.34 %
99.34 %
99.35 %
99.35 %
99.35 %
99.35 %
99.35 %
99.35 %
99.35 %
99.35 %
99.35 %
99.35 %
99.35 %
99.35 %
99.35 %
99.35 %
99.36 %
99.36 %
99.36 %
99.36 %
99.36 %
99.36 %
99.36 %
99.36 %
99.36 %
99.36 %
99.36 %
99.36 %
99.36 %
99.36 %
99.37 %
99.37 %
99.37 %
99.37 %
99.37 %
99.37 %
99.37 %
99.37 %
99.37 %
99.37 %
99.37 %
99.37 %
99.37 %
99.37 %
99.38 %
99.38 %
99.38 %
99.38 %
99.38 %
99.38 %
99.38 %
99.38 %
99.38 %
99.38 %
99.38 %
99.38 %
99.38 %
99.39 %
99.39 %
99.39 %
99.39 %
99.39 %
99.39 %
99.39 %
99.39 %
99.39 %
99.39 %
99.39 %
99.39 %
99.39 %
99

{('PRV55907', 'PRV55912'): [1, 12000.0, 1.67, 6.0, 0.33],
 ('PRV55907', 'PRV56046'): [1, 12000.0, 1.67, 6.0, 0.33],
 ('PRV55912', 'PRV56046'): [3, 25333.339999999997, 6.33, 24.66, 2.33],
 ('PRV55193', 'PRV55215'): [1, 65500.0, 2.0, 9.0, 1.5],
 ('PRV52283', 'PRV52283'): [15,
  123640.01,
  22.209999999999997,
  122.46999999999998,
  7.990000000000001],
 ('PRV54675', 'PRV54676'): [6, 30700.0, 8.25, 42.0, 2.75],
 ('PRV51342', 'PRV51393'): [2, 19333.33, 3.17, 15.0, 1.5],
 ('PRV51342', 'PRV55834'): [1, 11333.33, 1.67, 9.0, 1.0],
 ('PRV51393', 'PRV55834'): [1, 11333.33, 1.67, 9.0, 1.0],
 ('PRV53135', 'PRV53135'): [1, 8500.0, 1.5, 8.5, 0.5],
 ('PRV51842', 'PRV51842'): [35,
  305849.99,
  58.989999999999995,
  289.5,
  31.739999999999995],
 ('PRV51560', 'PRV51560'): [37,
  356749.99999999994,
  56.06999999999999,
  305.72999999999996,
  24.080000000000005],
 ('PRV51146', 'PRV51164'): [7, 39666.67, 10.83, 63.0, 3.83],
 ('PRV55670', 'PRV55907'): [4, 37166.66, 6.16, 34.510000000000005, 2.16],
 ('

In [19]:
edge_file_inp = pd.DataFrame.from_dict(graph_net_inp_count, orient='index', columns=['weight_count','weight_reimburse','weight_physician','weight_diagnosis','weight_procedure']).reset_index()

edge_file_inp['from'] = edge_file_inp['index'].apply(lambda x: x[0]).values
edge_file_inp['to'] = edge_file_inp['index'].apply(lambda x: x[1]).values
edge_file_inp = edge_file_inp[['from','to','weight_count','weight_reimburse','weight_physician','weight_diagnosis','weight_procedure']]
edge_file_inp.to_csv('Inpatient_edge.csv')
edge_file_inp

from        to  weight_count  weight_reimburse  weight_physician  \
0     PRV55907  PRV55912             1         12000.000             1.670   
1     PRV55907  PRV56046             1         12000.000             1.670   
2     PRV55912  PRV56046             3         25333.340             6.330   
3     PRV55193  PRV55215             1         65500.000             2.000   
4     PRV52283  PRV52283            15        123640.010            22.210   
...        ...       ...           ...               ...               ...   
5010  PRV51405  PRV51456             2         13000.000             2.500   
5011  PRV51405  PRV51508             1          6500.000             1.250   
5012  PRV51456  PRV51508             2         13000.000             2.500   
5013  PRV55215  PRV57295             1          6500.000             1.500   
5014  PRV51440  PRV51812             1          8500.000             2.500   

      weight_diagnosis  weight_procedure  
0                6.000             0.330  
1                6.000             0.330  
2               24.660             2.330  
3                9.000             1.500  
4              122.470             7.990  
...                ...               ...  
5010            18.000             0.500  
5011             9.000             0.250  
5012            18.000             0.500  
5013             7.000             1.500  
5014             9.500             1.000  

[5015 rows x 7 columns]

In [20]:
#Using Beneficiary as Edge for Provider
graph_net_out_count = {}
count = 0
total = len(df_bene)

for bene in df_bene.BeneID:
    count += 1
    print(round(count / total * 100,2), '%')
    sub_net = df_out.loc[df_out.BeneID == bene].sort_values(by='Provider').reset_index(drop=True)
    sub_net_p = sub_net.Provider
    sub_net_reimburse = round(sub_net.InscClaimAmtReimbursed.mean(),2)
    sub_net_phy = round(sub_net.NumberOfPhysician.mean(),2)
    sub_net_diag = round(sub_net.ClmDiagnosisCode_Count.mean(),2)
    sub_net_proce = round(sub_net.ClmProcedureCode_Count.mean(),2)
    pair_len = len(sub_net)
    if pair_len > 2:
        for providerx in range(pair_len):
            for providery in range(providerx+1,pair_len):
                if (sub_net_p[providerx],sub_net_p[providery]) in graph_net_out_count:
                    graph_net_out_count[(sub_net_p[providerx],sub_net_p[providery])][0] += 1
                    graph_net_out_count[(sub_net_p[providerx],sub_net_p[providery])][1] += sub_net_reimburse
                    graph_net_out_count[(sub_net_p[providerx],sub_net_p[providery])][2] += sub_net_phy
                    graph_net_out_count[(sub_net_p[providerx],sub_net_p[providery])][3] += sub_net_diag
                    graph_net_out_count[(sub_net_p[providerx],sub_net_p[providery])][4] += sub_net_proce
                else:
                    graph_net_out_count[(sub_net_p[providerx],sub_net_p[providery])] = []
                    graph_net_out_count[(sub_net_p[providerx],sub_net_p[providery])].append(1)
                    graph_net_out_count[(sub_net_p[providerx],sub_net_p[providery])].append(sub_net_reimburse)
                    graph_net_out_count[(sub_net_p[providerx],sub_net_p[providery])].append(sub_net_phy)
                    graph_net_out_count[(sub_net_p[providerx],sub_net_p[providery])].append(sub_net_diag)
                    graph_net_out_count[(sub_net_p[providerx],sub_net_p[providery])].append(sub_net_proce)
    elif pair_len == 2:
        p_from = sub_net.Provider[0]
        p_to = sub_net.Provider[1]
        if (p_from,p_to) in graph_net_out_count:
            graph_net_out_count[(p_from,p_to)][0] += 1
            graph_net_out_count[(p_from,p_to)][1] += sub_net_reimburse
            graph_net_out_count[(p_from,p_to)][2] += sub_net_phy
            graph_net_out_count[(p_from,p_to)][3] += sub_net_diag
            graph_net_out_count[(p_from,p_to)][4] += sub_net_proce
        else:
            graph_net_out_count[(p_from,p_to)] = []
            graph_net_out_count[(p_from,p_to)].append(1)
            graph_net_out_count[(p_from,p_to)].append(sub_net_reimburse)
            graph_net_out_count[(p_from,p_to)].append(sub_net_phy)
            graph_net_out_count[(p_from,p_to)].append(sub_net_diag)
            graph_net_out_count[(p_from,p_to)].append(sub_net_proce)
    else:
        pass
graph_net_out_count

0.0 %
0.0 %
0.0 %
0.0 %
0.0 %
0.0 %
0.01 %
0.01 %
0.01 %
0.01 %
0.01 %
0.01 %
0.01 %
0.01 %
0.01 %
0.01 %
0.01 %
0.01 %
0.01 %
0.01 %
0.02 %
0.02 %
0.02 %
0.02 %
0.02 %
0.02 %
0.02 %
0.02 %
0.02 %
0.02 %
0.02 %
0.02 %
0.02 %
0.02 %
0.03 %
0.03 %
0.03 %
0.03 %
0.03 %
0.03 %
0.03 %
0.03 %
0.03 %
0.03 %
0.03 %
0.03 %
0.03 %
0.03 %
0.04 %
0.04 %
0.04 %
0.04 %
0.04 %
0.04 %
0.04 %
0.04 %
0.04 %
0.04 %
0.04 %
0.04 %
0.04 %
0.04 %
0.05 %
0.05 %
0.05 %
0.05 %
0.05 %
0.05 %
0.05 %
0.05 %
0.05 %
0.05 %
0.05 %
0.05 %
0.05 %
0.05 %
0.06 %
0.06 %
0.06 %
0.06 %
0.06 %
0.06 %
0.06 %
0.06 %
0.06 %
0.06 %
0.06 %
0.06 %
0.06 %
0.06 %
0.07 %
0.07 %
0.07 %
0.07 %
0.07 %
0.07 %
0.07 %
0.07 %
0.07 %
0.07 %
0.07 %
0.07 %
0.07 %
0.08 %
0.08 %
0.08 %
0.08 %
0.08 %
0.08 %
0.08 %
0.08 %
0.08 %
0.08 %
0.08 %
0.08 %
0.08 %
0.08 %
0.09 %
0.09 %
0.09 %
0.09 %
0.09 %
0.09 %
0.09 %
0.09 %
0.09 %
0.09 %
0.09 %
0.09 %
0.09 %
0.09 %
0.1 %
0.1 %
0.1 %
0.1 %
0.1 %
0.1 %
0.1 %
0.1 %
0.1 %
0.1 %
0.1 %
0.1 %
0.1 %
0.1 %
0.11 

0.86 %
0.86 %
0.86 %
0.86 %
0.86 %
0.86 %
0.86 %
0.86 %
0.86 %
0.87 %
0.87 %
0.87 %
0.87 %
0.87 %
0.87 %
0.87 %
0.87 %
0.87 %
0.87 %
0.87 %
0.87 %
0.87 %
0.87 %
0.88 %
0.88 %
0.88 %
0.88 %
0.88 %
0.88 %
0.88 %
0.88 %
0.88 %
0.88 %
0.88 %
0.88 %
0.88 %
0.88 %
0.89 %
0.89 %
0.89 %
0.89 %
0.89 %
0.89 %
0.89 %
0.89 %
0.89 %
0.89 %
0.89 %
0.89 %
0.89 %
0.89 %
0.9 %
0.9 %
0.9 %
0.9 %
0.9 %
0.9 %
0.9 %
0.9 %
0.9 %
0.9 %
0.9 %
0.9 %
0.9 %
0.91 %
0.91 %
0.91 %
0.91 %
0.91 %
0.91 %
0.91 %
0.91 %
0.91 %
0.91 %
0.91 %
0.91 %
0.91 %
0.91 %
0.92 %
0.92 %
0.92 %
0.92 %
0.92 %
0.92 %
0.92 %
0.92 %
0.92 %
0.92 %
0.92 %
0.92 %
0.92 %
0.92 %
0.93 %
0.93 %
0.93 %
0.93 %
0.93 %
0.93 %
0.93 %
0.93 %
0.93 %
0.93 %
0.93 %
0.93 %
0.93 %
0.93 %
0.94 %
0.94 %
0.94 %
0.94 %
0.94 %
0.94 %
0.94 %
0.94 %
0.94 %
0.94 %
0.94 %
0.94 %
0.94 %
0.94 %
0.95 %
0.95 %
0.95 %
0.95 %
0.95 %
0.95 %
0.95 %
0.95 %
0.95 %
0.95 %
0.95 %
0.95 %
0.95 %
0.95 %
0.96 %
0.96 %
0.96 %
0.96 %
0.96 %
0.96 %
0.96 %
0.96 %
0.96 %
0.96 %
0.96 

1.72 %
1.72 %
1.72 %
1.72 %
1.72 %
1.72 %
1.72 %
1.72 %
1.72 %
1.72 %
1.73 %
1.73 %
1.73 %
1.73 %
1.73 %
1.73 %
1.73 %
1.73 %
1.73 %
1.73 %
1.73 %
1.73 %
1.73 %
1.74 %
1.74 %
1.74 %
1.74 %
1.74 %
1.74 %
1.74 %
1.74 %
1.74 %
1.74 %
1.74 %
1.74 %
1.74 %
1.74 %
1.75 %
1.75 %
1.75 %
1.75 %
1.75 %
1.75 %
1.75 %
1.75 %
1.75 %
1.75 %
1.75 %
1.75 %
1.75 %
1.75 %
1.76 %
1.76 %
1.76 %
1.76 %
1.76 %
1.76 %
1.76 %
1.76 %
1.76 %
1.76 %
1.76 %
1.76 %
1.76 %
1.76 %
1.77 %
1.77 %
1.77 %
1.77 %
1.77 %
1.77 %
1.77 %
1.77 %
1.77 %
1.77 %
1.77 %
1.77 %
1.77 %
1.77 %
1.78 %
1.78 %
1.78 %
1.78 %
1.78 %
1.78 %
1.78 %
1.78 %
1.78 %
1.78 %
1.78 %
1.78 %
1.78 %
1.78 %
1.79 %
1.79 %
1.79 %
1.79 %
1.79 %
1.79 %
1.79 %
1.79 %
1.79 %
1.79 %
1.79 %
1.79 %
1.79 %
1.79 %
1.8 %
1.8 %
1.8 %
1.8 %
1.8 %
1.8 %
1.8 %
1.8 %
1.8 %
1.8 %
1.8 %
1.8 %
1.8 %
1.81 %
1.81 %
1.81 %
1.81 %
1.81 %
1.81 %
1.81 %
1.81 %
1.81 %
1.81 %
1.81 %
1.81 %
1.81 %
1.81 %
1.82 %
1.82 %
1.82 %
1.82 %
1.82 %
1.82 %
1.82 %
1.82 %
1.82 %
1.82 %
1.82 

2.58 %
2.58 %
2.58 %
2.58 %
2.58 %
2.58 %
2.58 %
2.58 %
2.58 %
2.58 %
2.58 %
2.58 %
2.58 %
2.58 %
2.59 %
2.59 %
2.59 %
2.59 %
2.59 %
2.59 %
2.59 %
2.59 %
2.59 %
2.59 %
2.59 %
2.59 %
2.59 %
2.59 %
2.6 %
2.6 %
2.6 %
2.6 %
2.6 %
2.6 %
2.6 %
2.6 %
2.6 %
2.6 %
2.6 %
2.6 %
2.6 %
2.6 %
2.61 %
2.61 %
2.61 %
2.61 %
2.61 %
2.61 %
2.61 %
2.61 %
2.61 %
2.61 %
2.61 %
2.61 %
2.61 %
2.61 %
2.62 %
2.62 %
2.62 %
2.62 %
2.62 %
2.62 %
2.62 %
2.62 %
2.62 %
2.62 %
2.62 %
2.62 %
2.62 %
2.62 %
2.63 %
2.63 %
2.63 %
2.63 %
2.63 %
2.63 %
2.63 %
2.63 %
2.63 %
2.63 %
2.63 %
2.63 %
2.63 %
2.64 %
2.64 %
2.64 %
2.64 %
2.64 %
2.64 %
2.64 %
2.64 %
2.64 %
2.64 %
2.64 %
2.64 %
2.64 %
2.64 %
2.65 %
2.65 %
2.65 %
2.65 %
2.65 %
2.65 %
2.65 %
2.65 %
2.65 %
2.65 %
2.65 %
2.65 %
2.65 %
2.65 %
2.66 %
2.66 %
2.66 %
2.66 %
2.66 %
2.66 %
2.66 %
2.66 %
2.66 %
2.66 %
2.66 %
2.66 %
2.66 %
2.66 %
2.67 %
2.67 %
2.67 %
2.67 %
2.67 %
2.67 %
2.67 %
2.67 %
2.67 %
2.67 %
2.67 %
2.67 %
2.67 %
2.67 %
2.68 %
2.68 %
2.68 %
2.68 %
2.68 %
2.68 %

3.44 %
3.44 %
3.44 %
3.44 %
3.44 %
3.44 %
3.44 %
3.44 %
3.44 %
3.44 %
3.44 %
3.44 %
3.44 %
3.45 %
3.45 %
3.45 %
3.45 %
3.45 %
3.45 %
3.45 %
3.45 %
3.45 %
3.45 %
3.45 %
3.45 %
3.45 %
3.45 %
3.46 %
3.46 %
3.46 %
3.46 %
3.46 %
3.46 %
3.46 %
3.46 %
3.46 %
3.46 %
3.46 %
3.46 %
3.46 %
3.47 %
3.47 %
3.47 %
3.47 %
3.47 %
3.47 %
3.47 %
3.47 %
3.47 %
3.47 %
3.47 %
3.47 %
3.47 %
3.47 %
3.48 %
3.48 %
3.48 %
3.48 %
3.48 %
3.48 %
3.48 %
3.48 %
3.48 %
3.48 %
3.48 %
3.48 %
3.48 %
3.48 %
3.49 %
3.49 %
3.49 %
3.49 %
3.49 %
3.49 %
3.49 %
3.49 %
3.49 %
3.49 %
3.49 %
3.49 %
3.49 %
3.49 %
3.5 %
3.5 %
3.5 %
3.5 %
3.5 %
3.5 %
3.5 %
3.5 %
3.5 %
3.5 %
3.5 %
3.5 %
3.5 %
3.5 %
3.51 %
3.51 %
3.51 %
3.51 %
3.51 %
3.51 %
3.51 %
3.51 %
3.51 %
3.51 %
3.51 %
3.51 %
3.51 %
3.51 %
3.52 %
3.52 %
3.52 %
3.52 %
3.52 %
3.52 %
3.52 %
3.52 %
3.52 %
3.52 %
3.52 %
3.52 %
3.52 %
3.52 %
3.53 %
3.53 %
3.53 %
3.53 %
3.53 %
3.53 %
3.53 %
3.53 %
3.53 %
3.53 %
3.53 %
3.53 %
3.53 %
3.54 %
3.54 %
3.54 %
3.54 %
3.54 %
3.54 %
3.54 %
3.54 %

...

97.48 %
97.48 %
97.48 %
97.48 %
97.48 %
97.48 %
97.48 %
97.48 %
97.48 %
97.48 %
97.48 %
97.48 %
97.48 %
97.48 %
97.49 %
97.49 %
97.49 %
97.49 %
97.49 %
97.49 %
97.49 %
97.49 %
97.49 %
97.49 %
97.49 %
97.49 %
97.49 %
97.49 %
97.5 %
97.5 %
97.5 %
97.5 %
97.5 %
97.5 %
97.5 %
97.5 %
97.5 %
97.5 %
97.5 %
97.5 %
97.5 %
97.5 %
97.51 %
97.51 %
97.51 %
97.51 %
97.51 %
97.51 %
97.51 %
97.51 %
97.51 %
97.51 %
97.51 %
97.51 %
97.51 %
97.52 %
97.52 %
97.52 %
97.52 %
97.52 %
97.52 %
97.52 %
97.52 %
97.52 %
97.52 %
97.52 %
97.52 %
97.52 %
97.52 %
97.53 %
97.53 %
97.53 %
97.53 %
97.53 %
97.53 %
97.53 %
97.53 %
97.53 %
97.53 %
97.53 %
97.53 %
97.53 %
97.53 %
97.54 %
97.54 %
97.54 %
97.54 %
97.54 %
97.54 %
97.54 %
97.54 %
97.54 %
97.54 %
97.54 %
97.54 %
97.54 %
97.54 %
97.55 %
97.55 %
97.55 %
97.55 %
97.55 %
97.55 %
97.55 %
97.55 %
97.55 %
97.55 %
97.55 %
97.55 %
97.55 %
97.55 %
97.56 %
97.56 %
97.56 %
97.56 %
97.56 %
97.56 %
97.56 %
97.56 %
97.56 %
97.56 %
97.56 %
97.56 %
97.56 %
97.56 %
97.57 %
97.57 

98.23 %
98.23 %
98.23 %
98.23 %
98.23 %
98.23 %
98.23 %
98.23 %
98.23 %
98.23 %
98.23 %
98.23 %
98.23 %
98.23 %
98.24 %
98.24 %
98.24 %
98.24 %
98.24 %
98.24 %
98.24 %
98.24 %
98.24 %
98.24 %
98.24 %
98.24 %
98.24 %
98.24 %
98.25 %
98.25 %
98.25 %
98.25 %
98.25 %
98.25 %
98.25 %
98.25 %
98.25 %
98.25 %
98.25 %
98.25 %
98.25 %
98.25 %
98.26 %
98.26 %
98.26 %
98.26 %
98.26 %
98.26 %
98.26 %
98.26 %
98.26 %
98.26 %
98.26 %
98.26 %
98.26 %
98.26 %
98.27 %
98.27 %
98.27 %
98.27 %
98.27 %
98.27 %
98.27 %
98.27 %
98.27 %
98.27 %
98.27 %
98.27 %
98.27 %
98.28 %
98.28 %
98.28 %
98.28 %
98.28 %
98.28 %
98.28 %
98.28 %
98.28 %
98.28 %
98.28 %
98.28 %
98.28 %
98.28 %
98.29 %
98.29 %
98.29 %
98.29 %
98.29 %
98.29 %
98.29 %
98.29 %
98.29 %
98.29 %
98.29 %
98.29 %
98.29 %
98.29 %
98.3 %
98.3 %
98.3 %
98.3 %
98.3 %
98.3 %
98.3 %
98.3 %
98.3 %
98.3 %
98.3 %
98.3 %
98.3 %
98.3 %
98.31 %
98.31 %
98.31 %
98.31 %
98.31 %
98.31 %
98.31 %
98.31 %
98.31 %
98.31 %
98.31 %
98.31 %
98.31 %
98.31 %
98.32 %
98.32 

98.98 %
98.98 %
98.98 %
98.98 %
98.98 %
98.98 %
98.98 %
98.98 %
98.98 %
98.98 %
98.98 %
98.98 %
98.99 %
98.99 %
98.99 %
98.99 %
98.99 %
98.99 %
98.99 %
98.99 %
98.99 %
98.99 %
98.99 %
98.99 %
98.99 %
98.99 %
99.0 %
99.0 %
99.0 %
99.0 %
99.0 %
99.0 %
99.0 %
99.0 %
99.0 %
99.0 %
99.0 %
99.0 %
99.0 %
99.0 %
99.01 %
99.01 %
99.01 %
99.01 %
99.01 %
99.01 %
99.01 %
99.01 %
99.01 %
99.01 %
99.01 %
99.01 %
99.01 %
99.01 %
99.02 %
99.02 %
99.02 %
99.02 %
99.02 %
99.02 %
99.02 %
99.02 %
99.02 %
99.02 %
99.02 %
99.02 %
99.02 %
99.02 %
99.03 %
99.03 %
99.03 %
99.03 %
99.03 %
99.03 %
99.03 %
99.03 %
99.03 %
99.03 %
99.03 %
99.03 %
99.03 %
99.04 %
99.04 %
99.04 %
99.04 %
99.04 %
99.04 %
99.04 %
99.04 %
99.04 %
99.04 %
99.04 %
99.04 %
99.04 %
99.04 %
99.05 %
99.05 %
99.05 %
99.05 %
99.05 %
99.05 %
99.05 %
99.05 %
99.05 %
99.05 %
99.05 %
99.05 %
99.05 %
99.05 %
99.06 %
99.06 %
99.06 %
99.06 %
99.06 %
99.06 %
99.06 %
99.06 %
99.06 %
99.06 %
99.06 %
99.06 %
99.06 %
99.06 %
99.07 %
99.07 %
99.07 %
99.07 

99.73 %
99.73 %
99.73 %
99.73 %
99.73 %
99.73 %
99.73 %
99.73 %
99.73 %
99.73 %
99.73 %
99.73 %
99.74 %
99.74 %
99.74 %
99.74 %
99.74 %
99.74 %
99.74 %
99.74 %
99.74 %
99.74 %
99.74 %
99.74 %
99.74 %
99.74 %
99.75 %
99.75 %
99.75 %
99.75 %
99.75 %
99.75 %
99.75 %
99.75 %
99.75 %
99.75 %
99.75 %
99.75 %
99.75 %
99.75 %
99.76 %
99.76 %
99.76 %
99.76 %
99.76 %
99.76 %
99.76 %
99.76 %
99.76 %
99.76 %
99.76 %
99.76 %
99.76 %
99.76 %
99.77 %
99.77 %
99.77 %
99.77 %
99.77 %
99.77 %
99.77 %
99.77 %
99.77 %
99.77 %
99.77 %
99.77 %
99.77 %
99.77 %
99.78 %
99.78 %
99.78 %
99.78 %
99.78 %
99.78 %
99.78 %
99.78 %
99.78 %
99.78 %
99.78 %
99.78 %
99.78 %
99.78 %
99.79 %
99.79 %
99.79 %
99.79 %
99.79 %
99.79 %
99.79 %
99.79 %
99.79 %
99.79 %
99.79 %
99.79 %
99.79 %
99.8 %
99.8 %
99.8 %
99.8 %
99.8 %
99.8 %
99.8 %
99.8 %
99.8 %
99.8 %
99.8 %
99.8 %
99.8 %
99.8 %
99.81 %
99.81 %
99.81 %
99.81 %
99.81 %
99.81 %
99.81 %
99.81 %
99.81 %
99.81 %
99.81 %
99.81 %
99.81 %
99.81 %
99.82 %
99.82 %
99.82 %
99.82 

{('PRV57595', 'PRV57610'): [25,
  8663.5,
  42.37999999999998,
  78.38000000000001,
  0.0],
 ('PRV55903', 'PRV55951'): [1, 150.83, 1.58, 3.25, 0.0],
 ('PRV55903', 'PRV56011'): [63,
  14580.169999999993,
  101.38999999999996,
  159.59,
  0.0],
 ('PRV55951', 'PRV56011'): [103,
  26619.160000000018,
  167.92999999999992,
  296.08000000000004,
  0.0],
 ('PRV56011', 'PRV56011'): [4670,
  1359510.0600000066,
  7288.1800000000485,
  12659.52,
  0.0],
 ('PRV52038', 'PRV54064'): [1, 223.75, 1.38, 3.25, 0.0],
 ('PRV52038', 'PRV54080'): [6, 1342.5, 8.28, 19.5, 0.0],
 ('PRV54064', 'PRV54080'): [362,
  224885.4400000004,
  530.1899999999993,
  1064.1099999999988,
  0.0],
 ('PRV54080', 'PRV54080'): [807,
  304380.1799999991,
  1210.2100000000041,
  2301.5500000000056,
  2.1000000000000005],
 ('PRV56559', 'PRV56559'): [399,
  139026.24,
  635.3200000000007,
  1075.5800000000004,
  0.6000000000000001],
 ('PRV56559', 'PRV56743'): [318,
  112963.11,
  489.81999999999977,
  895.8700000000007,
  0.0],
 ('

In [21]:
edge_file_out = pd.DataFrame.from_dict(graph_net_out_count, orient='index', columns=['weight_count','weight_reimburse','weight_physician','weight_diagnosis','weight_procedure']).reset_index()

edge_file_out['from'] = edge_file_out['index'].apply(lambda x: x[0]).values
edge_file_out['to'] = edge_file_out['index'].apply(lambda x: x[1]).values
edge_file_out = edge_file_out[['from','to','weight_count','weight_reimburse','weight_physician','weight_diagnosis','weight_procedure']]
edge_file_out.to_csv('Outpatient_edge.csv')
edge_file_out

from        to  weight_count  weight_reimburse  weight_physician  \
0       PRV57595  PRV57610            25          8663.500            42.380   
1       PRV55903  PRV55951             1           150.830             1.580   
2       PRV55903  PRV56011            63         14580.170           101.390   
3       PRV55951  PRV56011           103         26619.160           167.930   
4       PRV56011  PRV56011          4670       1359510.060          7288.180   
...          ...       ...           ...               ...               ...   
149922  PRV54668  PRV54894             1            80.000             1.000   
149923  PRV52021  PRV55913             1           200.000             2.500   
149924  PRV51836  PRV54337            11          2545.730            19.690   
149925  PRV51851  PRV54337             1           231.430             1.790   
149926  PRV51908  PRV54337             1           231.430             1.790   

        weight_diagnosis  weight_procedure  
0                 78.380             0.000  
1                  3.250             0.000  
2                159.590             0.000  
3                296.080             0.000  
4              12659.520             0.000  
...                  ...               ...  
149922             2.000             0.000  
149923             2.000             0.000  
149924            30.690             0.000  
149925             2.790             0.000  
149926             2.790             0.000  

[149927 rows x 7 columns]

In [22]:
#Using Beneficiary as Edge for Provider
graph_net_count = {}
count = 0
total = len(df_bene)

for bene in df_bene.BeneID:
    count += 1
    print(round(count / total * 100,2), '%')
    sub_net = df.loc[df.BeneID == bene].sort_values(by='Provider').reset_index(drop=True)
    sub_net_p = sub_net.Provider
    sub_net_reimburse = round(sub_net.InscClaimAmtReimbursed.mean(),2)
    sub_net_phy = round(sub_net.NumberOfPhysician.mean(),2)
    sub_net_diag = round(sub_net.ClmDiagnosisCode_Count.mean(),2)
    sub_net_proce = round(sub_net.ClmProcedureCode_Count.mean(),2)
    pair_len = len(sub_net)
    if pair_len > 2:
        for providerx in range(pair_len):
            for providery in range(providerx+1,pair_len):
                if (sub_net_p[providerx],sub_net_p[providery]) in graph_net_count:
                    graph_net_count[(sub_net_p[providerx],sub_net_p[providery])][0] += 1
                    graph_net_count[(sub_net_p[providerx],sub_net_p[providery])][1] += sub_net_reimburse
                    graph_net_count[(sub_net_p[providerx],sub_net_p[providery])][2] += sub_net_phy
                    graph_net_count[(sub_net_p[providerx],sub_net_p[providery])][3] += sub_net_diag
                    graph_net_count[(sub_net_p[providerx],sub_net_p[providery])][4] += sub_net_proce
                else:
                    graph_net_count[(sub_net_p[providerx],sub_net_p[providery])] = []
                    graph_net_count[(sub_net_p[providerx],sub_net_p[providery])].append(1)
                    graph_net_count[(sub_net_p[providerx],sub_net_p[providery])].append(sub_net_reimburse)
                    graph_net_count[(sub_net_p[providerx],sub_net_p[providery])].append(sub_net_phy)
                    graph_net_count[(sub_net_p[providerx],sub_net_p[providery])].append(sub_net_diag)
                    graph_net_count[(sub_net_p[providerx],sub_net_p[providery])].append(sub_net_proce)
    elif pair_len == 2:
        p_from = sub_net.Provider[0]
        p_to = sub_net.Provider[1]
        if (p_from,p_to) in graph_net_count:
            graph_net_count[(p_from,p_to)][0] += 1
            graph_net_count[(p_from,p_to)][1] += sub_net_reimburse
            graph_net_count[(p_from,p_to)][2] += sub_net_phy
            graph_net_count[(p_from,p_to)][3] += sub_net_diag
            graph_net_count[(p_from,p_to)][4] += sub_net_proce
        else:
            graph_net_count[(p_from,p_to)] = []
            graph_net_count[(p_from,p_to)].append(1)
            graph_net_count[(p_from,p_to)].append(sub_net_reimburse)
            graph_net_count[(p_from,p_to)].append(sub_net_phy)
            graph_net_count[(p_from,p_to)].append(sub_net_diag)
            graph_net_count[(p_from,p_to)].append(sub_net_proce)
    else:
        pass
graph_net_count

0.0 %
0.0 %
0.0 %
0.0 %
0.0 %
0.0 %
0.01 %
0.01 %
0.01 %
0.01 %
0.01 %
0.01 %
0.01 %
0.01 %
0.01 %
0.01 %
0.01 %
0.01 %
0.01 %
0.01 %
0.02 %
0.02 %
0.02 %
0.02 %
0.02 %
0.02 %
0.02 %
0.02 %
0.02 %
0.02 %
0.02 %
0.02 %
0.02 %
0.02 %
0.03 %
0.03 %
0.03 %
0.03 %
0.03 %
0.03 %
0.03 %
0.03 %
0.03 %
0.03 %
0.03 %
0.03 %
0.03 %
0.03 %
0.04 %
0.04 %
0.04 %
0.04 %
0.04 %
0.04 %
0.04 %
0.04 %
0.04 %
0.04 %
0.04 %
0.04 %
0.04 %
0.04 %
0.05 %
0.05 %
0.05 %
0.05 %
0.05 %
0.05 %
0.05 %
0.05 %
0.05 %
0.05 %
0.05 %
0.05 %
0.05 %
0.05 %
0.06 %
0.06 %
0.06 %
0.06 %
0.06 %
0.06 %
0.06 %
0.06 %
0.06 %
0.06 %
0.06 %
0.06 %
0.06 %
0.06 %
0.07 %
0.07 %
0.07 %
0.07 %
0.07 %
0.07 %
0.07 %
0.07 %
0.07 %
0.07 %
0.07 %
0.07 %
0.07 %
0.08 %
0.08 %
0.08 %
0.08 %
0.08 %
0.08 %
0.08 %
0.08 %
0.08 %
0.08 %
0.08 %
0.08 %
0.08 %
0.08 %
0.09 %
0.09 %
0.09 %
0.09 %
0.09 %
0.09 %
0.09 %
0.09 %
0.09 %
0.09 %
0.09 %
0.09 %
0.09 %
0.09 %
0.1 %
0.1 %
0.1 %
0.1 %
0.1 %
0.1 %
0.1 %
0.1 %
0.1 %
0.1 %
0.1 %
0.1 %
0.1 %
0.1 %
0.11 

0.86 %
0.86 %
0.86 %
0.86 %
0.86 %
0.86 %
0.86 %
0.86 %
0.86 %
0.87 %
0.87 %
0.87 %
0.87 %
0.87 %
0.87 %
0.87 %
0.87 %
0.87 %
0.87 %
0.87 %
0.87 %
0.87 %
0.87 %
0.88 %
0.88 %
0.88 %
0.88 %
0.88 %
0.88 %
0.88 %
0.88 %
0.88 %
0.88 %
0.88 %
0.88 %
0.88 %
0.88 %
0.89 %
0.89 %
0.89 %
0.89 %
0.89 %
0.89 %
0.89 %
0.89 %
0.89 %
0.89 %
0.89 %
0.89 %
0.89 %
0.89 %
0.9 %
0.9 %
0.9 %
0.9 %
0.9 %
0.9 %
0.9 %
0.9 %
0.9 %
0.9 %
0.9 %
0.9 %
0.9 %
0.91 %
0.91 %
0.91 %
0.91 %
0.91 %
0.91 %
0.91 %
0.91 %
0.91 %
0.91 %
0.91 %
0.91 %
0.91 %
0.91 %
0.92 %
0.92 %
0.92 %
0.92 %
0.92 %
0.92 %
0.92 %
0.92 %
0.92 %
0.92 %
0.92 %
0.92 %
0.92 %
0.92 %
0.93 %
0.93 %
0.93 %
0.93 %
0.93 %
0.93 %
0.93 %
0.93 %
0.93 %
0.93 %
0.93 %
0.93 %
0.93 %
0.93 %
0.94 %
0.94 %
0.94 %
0.94 %
0.94 %
0.94 %
0.94 %
0.94 %
0.94 %
0.94 %
0.94 %
0.94 %
0.94 %
0.94 %
0.95 %
0.95 %
0.95 %
0.95 %
0.95 %
0.95 %
0.95 %
0.95 %
0.95 %
0.95 %
0.95 %
0.95 %
0.95 %
0.95 %
0.96 %
0.96 %
0.96 %
0.96 %
0.96 %
0.96 %
0.96 %
0.96 %
0.96 %
0.96 %
0.96 

1.72 %
1.72 %
1.72 %
1.72 %
1.72 %
1.73 %
1.73 %
1.73 %
1.73 %
1.73 %
1.73 %
1.73 %
1.73 %
1.73 %
1.73 %
1.73 %
1.73 %
1.73 %
1.74 %
1.74 %
1.74 %
1.74 %
1.74 %
1.74 %
1.74 %
1.74 %
1.74 %
1.74 %
1.74 %
1.74 %
1.74 %
1.74 %
1.75 %
1.75 %
1.75 %
1.75 %
1.75 %
1.75 %
1.75 %
1.75 %
1.75 %
1.75 %
1.75 %
1.75 %
1.75 %
1.75 %
1.76 %
1.76 %
1.76 %
1.76 %
1.76 %
1.76 %
1.76 %
1.76 %
1.76 %
1.76 %
1.76 %
1.76 %
1.76 %
1.76 %
1.77 %
1.77 %
1.77 %
1.77 %
1.77 %
1.77 %
1.77 %
1.77 %
1.77 %
1.77 %
1.77 %
1.77 %
1.77 %
1.77 %
1.78 %
1.78 %
1.78 %
1.78 %
1.78 %
1.78 %
1.78 %
1.78 %
1.78 %
1.78 %
1.78 %
1.78 %
1.78 %
1.78 %
1.79 %
1.79 %
1.79 %
1.79 %
1.79 %
1.79 %
1.79 %
1.79 %
1.79 %
1.79 %
1.79 %
1.79 %
1.79 %
1.79 %
1.8 %
1.8 %
1.8 %
1.8 %
1.8 %
1.8 %
1.8 %
1.8 %
1.8 %
1.8 %
1.8 %
1.8 %
1.8 %
1.81 %
1.81 %
1.81 %
1.81 %
1.81 %
1.81 %
1.81 %
1.81 %
1.81 %
1.81 %
1.81 %
1.81 %
1.81 %
1.81 %
1.82 %
1.82 %
1.82 %
1.82 %
1.82 %
1.82 %
1.82 %
1.82 %
1.82 %
1.82 %
1.82 %
1.82 %
1.82 %
1.82 %
1.83 %
1.83 

2.58 %
2.58 %
2.58 %
2.58 %
2.58 %
2.58 %
2.58 %
2.59 %
2.59 %
2.59 %
2.59 %
2.59 %
2.59 %
2.59 %
2.59 %
2.59 %
2.59 %
2.59 %
2.59 %
2.59 %
2.59 %
2.6 %
2.6 %
2.6 %
2.6 %
2.6 %
2.6 %
2.6 %
2.6 %
2.6 %
2.6 %
2.6 %
2.6 %
2.6 %
2.6 %
2.61 %
2.61 %
2.61 %
2.61 %
2.61 %
2.61 %
2.61 %
2.61 %
2.61 %
2.61 %
2.61 %
2.61 %
2.61 %
2.61 %
2.62 %
2.62 %
2.62 %
2.62 %
2.62 %
2.62 %
2.62 %
2.62 %
2.62 %
2.62 %
2.62 %
2.62 %
2.62 %
2.62 %
2.63 %
2.63 %
2.63 %
2.63 %
2.63 %
2.63 %
2.63 %
2.63 %
2.63 %
2.63 %
2.63 %
2.63 %
2.63 %
2.64 %
2.64 %
2.64 %
2.64 %
2.64 %
2.64 %
2.64 %
2.64 %
2.64 %
2.64 %
2.64 %
2.64 %
2.64 %
2.64 %
2.65 %
2.65 %
2.65 %
2.65 %
2.65 %
2.65 %
2.65 %
2.65 %
2.65 %
2.65 %
2.65 %
2.65 %
2.65 %
2.65 %
2.66 %
2.66 %
2.66 %
2.66 %
2.66 %
2.66 %
2.66 %
2.66 %
2.66 %
2.66 %
2.66 %
2.66 %
2.66 %
2.66 %
2.67 %
2.67 %
2.67 %
2.67 %
2.67 %
2.67 %
2.67 %
2.67 %
2.67 %
2.67 %
2.67 %
2.67 %
2.67 %
2.67 %
2.68 %
2.68 %
2.68 %
2.68 %
2.68 %
2.68 %
2.68 %
2.68 %
2.68 %
2.68 %
2.68 %
2.68 %
2.68 %

3.44 %
3.44 %
3.44 %
3.44 %
3.45 %
3.45 %
3.45 %
3.45 %
3.45 %
3.45 %
3.45 %
3.45 %
3.45 %
3.45 %
3.45 %
3.45 %
3.45 %
3.45 %
3.46 %
3.46 %
3.46 %
3.46 %
3.46 %
3.46 %
3.46 %
3.46 %
3.46 %
3.46 %
3.46 %
3.46 %
3.46 %
3.47 %
3.47 %
3.47 %
3.47 %
3.47 %
3.47 %
3.47 %
3.47 %
3.47 %
3.47 %
3.47 %
3.47 %
3.47 %
3.47 %
3.48 %
3.48 %
3.48 %
3.48 %
3.48 %
3.48 %
3.48 %
3.48 %
3.48 %
3.48 %
3.48 %
3.48 %
3.48 %
3.48 %
3.49 %
3.49 %
3.49 %
3.49 %
3.49 %
3.49 %
3.49 %
3.49 %
3.49 %
3.49 %
3.49 %
3.49 %
3.49 %
3.49 %
3.5 %
3.5 %
3.5 %
3.5 %
3.5 %
3.5 %
3.5 %
3.5 %
3.5 %
3.5 %
3.5 %
3.5 %
3.5 %
3.5 %
3.51 %
3.51 %
3.51 %
3.51 %
3.51 %
3.51 %
3.51 %
3.51 %
3.51 %
3.51 %
3.51 %
3.51 %
3.51 %
3.51 %
3.52 %
3.52 %
3.52 %
3.52 %
3.52 %
3.52 %
3.52 %
3.52 %
3.52 %
3.52 %
3.52 %
3.52 %
3.52 %
3.52 %
3.53 %
3.53 %
3.53 %
3.53 %
3.53 %
3.53 %
3.53 %
3.53 %
3.53 %
3.53 %
3.53 %
3.53 %
3.53 %
3.54 %
3.54 %
3.54 %
3.54 %
3.54 %
3.54 %
3.54 %
3.54 %
3.54 %
3.54 %
3.54 %
3.54 %
3.54 %
3.54 %
3.55 %
3.55 %
3.55 %

...

97.44 %
97.44 %
97.44 %
97.44 %
97.44 %
97.44 %
97.44 %
97.44 %
97.44 %
97.44 %
97.45 %
97.45 %
97.45 %
97.45 %
97.45 %
97.45 %
97.45 %
97.45 %
97.45 %
97.45 %
97.45 %
97.45 %
97.45 %
97.45 %
97.46 %
97.46 %
97.46 %
97.46 %
97.46 %
97.46 %
97.46 %
97.46 %
97.46 %
97.46 %
97.46 %
97.46 %
97.46 %
97.46 %
97.47 %
97.47 %
97.47 %
97.47 %
97.47 %
97.47 %
97.47 %
97.47 %
97.47 %
97.47 %
97.47 %
97.47 %
97.47 %
97.47 %
97.48 %
97.48 %
97.48 %
97.48 %
97.48 %
97.48 %
97.48 %
97.48 %
97.48 %
97.48 %
97.48 %
97.48 %
97.48 %
97.48 %
97.49 %
97.49 %
97.49 %
97.49 %
97.49 %
97.49 %
97.49 %
97.49 %
97.49 %
97.49 %
97.49 %
97.49 %
97.49 %
97.49 %
97.5 %
97.5 %
97.5 %
97.5 %
97.5 %
97.5 %
97.5 %
97.5 %
97.5 %
97.5 %
97.5 %
97.5 %
97.5 %
97.5 %
97.51 %
97.51 %
97.51 %
97.51 %
97.51 %
97.51 %
97.51 %
97.51 %
97.51 %
97.51 %
97.51 %
97.51 %
97.51 %
97.52 %
97.52 %
97.52 %
97.52 %
97.52 %
97.52 %
97.52 %
97.52 %
97.52 %
97.52 %
97.52 %
97.52 %
97.52 %
97.52 %
97.53 %
97.53 %
97.53 %
97.53 %
97.53 %
97.53 

98.19 %
98.19 %
98.19 %
98.19 %
98.19 %
98.2 %
98.2 %
98.2 %
98.2 %
98.2 %
98.2 %
98.2 %
98.2 %
98.2 %
98.2 %
98.2 %
98.2 %
98.2 %
98.21 %
98.21 %
98.21 %
98.21 %
98.21 %
98.21 %
98.21 %
98.21 %
98.21 %
98.21 %
98.21 %
98.21 %
98.21 %
98.21 %
98.22 %
98.22 %
98.22 %
98.22 %
98.22 %
98.22 %
98.22 %
98.22 %
98.22 %
98.22 %
98.22 %
98.22 %
98.22 %
98.22 %
98.23 %
98.23 %
98.23 %
98.23 %
98.23 %
98.23 %
98.23 %
98.23 %
98.23 %
98.23 %
98.23 %
98.23 %
98.23 %
98.23 %
98.24 %
98.24 %
98.24 %
98.24 %
98.24 %
98.24 %
98.24 %
98.24 %
98.24 %
98.24 %
98.24 %
98.24 %
98.24 %
98.24 %
98.25 %
98.25 %
98.25 %
98.25 %
98.25 %
98.25 %
98.25 %
98.25 %
98.25 %
98.25 %
98.25 %
98.25 %
98.25 %
98.25 %
98.26 %
98.26 %
98.26 %
98.26 %
98.26 %
98.26 %
98.26 %
98.26 %
98.26 %
98.26 %
98.26 %
98.26 %
98.26 %
98.26 %
98.27 %
98.27 %
98.27 %
98.27 %
98.27 %
98.27 %
98.27 %
98.27 %
98.27 %
98.27 %
98.27 %
98.27 %
98.27 %
98.28 %
98.28 %
98.28 %
98.28 %
98.28 %
98.28 %
98.28 %
98.28 %
98.28 %
98.28 %
98.28 %
98.28

98.94 %
98.94 %
98.94 %
98.94 %
98.95 %
98.95 %
98.95 %
98.95 %
98.95 %
98.95 %
98.95 %
98.95 %
98.95 %
98.95 %
98.95 %
98.95 %
98.95 %
98.95 %
98.96 %
98.96 %
98.96 %
98.96 %
98.96 %
98.96 %
98.96 %
98.96 %
98.96 %
98.96 %
98.96 %
98.96 %
98.96 %
98.97 %
98.97 %
98.97 %
98.97 %
98.97 %
98.97 %
98.97 %
98.97 %
98.97 %
98.97 %
98.97 %
98.97 %
98.97 %
98.97 %
98.98 %
98.98 %
98.98 %
98.98 %
98.98 %
98.98 %
98.98 %
98.98 %
98.98 %
98.98 %
98.98 %
98.98 %
98.98 %
98.98 %
98.99 %
98.99 %
98.99 %
98.99 %
98.99 %
98.99 %
98.99 %
98.99 %
98.99 %
98.99 %
98.99 %
98.99 %
98.99 %
98.99 %
99.0 %
99.0 %
99.0 %
99.0 %
99.0 %
99.0 %
99.0 %
99.0 %
99.0 %
99.0 %
99.0 %
99.0 %
99.0 %
99.0 %
99.01 %
99.01 %
99.01 %
99.01 %
99.01 %
99.01 %
99.01 %
99.01 %
99.01 %
99.01 %
99.01 %
99.01 %
99.01 %
99.01 %
99.02 %
99.02 %
99.02 %
99.02 %
99.02 %
99.02 %
99.02 %
99.02 %
99.02 %
99.02 %
99.02 %
99.02 %
99.02 %
99.02 %
99.03 %
99.03 %
99.03 %
99.03 %
99.03 %
99.03 %
99.03 %
99.03 %
99.03 %
99.03 %
99.03 %
99.03 

99.7 %
99.7 %
99.7 %
99.7 %
99.7 %
99.7 %
99.7 %
99.7 %
99.7 %
99.7 %
99.7 %
99.7 %
99.7 %
99.71 %
99.71 %
99.71 %
99.71 %
99.71 %
99.71 %
99.71 %
99.71 %
99.71 %
99.71 %
99.71 %
99.71 %
99.71 %
99.71 %
99.72 %
99.72 %
99.72 %
99.72 %
99.72 %
99.72 %
99.72 %
99.72 %
99.72 %
99.72 %
99.72 %
99.72 %
99.72 %
99.73 %
99.73 %
99.73 %
99.73 %
99.73 %
99.73 %
99.73 %
99.73 %
99.73 %
99.73 %
99.73 %
99.73 %
99.73 %
99.73 %
99.74 %
99.74 %
99.74 %
99.74 %
99.74 %
99.74 %
99.74 %
99.74 %
99.74 %
99.74 %
99.74 %
99.74 %
99.74 %
99.74 %
99.75 %
99.75 %
99.75 %
99.75 %
99.75 %
99.75 %
99.75 %
99.75 %
99.75 %
99.75 %
99.75 %
99.75 %
99.75 %
99.75 %
99.76 %
99.76 %
99.76 %
99.76 %
99.76 %
99.76 %
99.76 %
99.76 %
99.76 %
99.76 %
99.76 %
99.76 %
99.76 %
99.76 %
99.77 %
99.77 %
99.77 %
99.77 %
99.77 %
99.77 %
99.77 %
99.77 %
99.77 %
99.77 %
99.77 %
99.77 %
99.77 %
99.77 %
99.78 %
99.78 %
99.78 %
99.78 %
99.78 %
99.78 %
99.78 %
99.78 %
99.78 %
99.78 %
99.78 %
99.78 %
99.78 %
99.78 %
99.79 %
99.79 %
99.79

{('PRV55907', 'PRV55912'): [1, 12000.0, 1.67, 6.0, 0.33],
 ('PRV55907', 'PRV56046'): [1, 12000.0, 1.67, 6.0, 0.33],
 ('PRV55912', 'PRV56046'): [3, 22350.0, 5.67, 21.5, 1.83],
 ('PRV57595', 'PRV57610'): [25,
  15343.500000000002,
  42.539999999999985,
  81.22,
  0.5],
 ('PRV55903', 'PRV55951'): [2, 1218.33, 3.08, 6.5, 0.25],
 ('PRV55903', 'PRV56011'): [151,
  178382.73000000013,
  233.48999999999987,
  510.8400000000002,
  11.35],
 ('PRV55951', 'PRV56011'): [126,
  131036.78999999992,
  205.27999999999994,
  412.6900000000002,
  7.3699999999999966],
 ('PRV56011', 'PRV56011'): [4670,
  3225699.910000033,
  7320.87999999997,
  13698.610000000146,
  133.7599999999984],
 ('PRV52038', 'PRV54064'): [1, 223.75, 1.38, 3.25, 0.0],
 ('PRV52038', 'PRV54080'): [6, 1342.5, 8.28, 19.5, 0.0],
 ('PRV54064', 'PRV54080'): [430,
  703164.5900000007,
  647.4400000000019,
  1441.1300000000056,
  38.55],
 ('PRV54080', 'PRV54080'): [807,
  764364.6399999976,
  1221.4799999999968,
  2508.8300000000036,
  38.57

In [23]:
edge_file = pd.DataFrame.from_dict(graph_net_count, orient='index', columns=['weight_count','weight_reimburse','weight_physician','weight_diagnosis','weight_procedure']).reset_index()

edge_file['from'] = edge_file['index'].apply(lambda x: x[0]).values
edge_file['to'] = edge_file['index'].apply(lambda x: x[1]).values
edge_file = edge_file[['from','to','weight_count','weight_reimburse','weight_physician','weight_diagnosis','weight_procedure']]
edge_file.to_csv('Patient_edge.csv')
edge_file

from        to  weight_count  weight_reimburse  weight_physician  \
0       PRV55907  PRV55912             1         12000.000             1.670   
1       PRV55907  PRV56046             1         12000.000             1.670   
2       PRV55912  PRV56046             3         22350.000             5.670   
3       PRV57595  PRV57610            25         15343.500            42.540   
4       PRV55903  PRV55951             2          1218.330             3.080   
...          ...       ...           ...               ...               ...   
171774  PRV54668  PRV54894             1            80.000             1.000   
171775  PRV52021  PRV55913             1           200.000             2.500   
171776  PRV51836  PRV54337            11          2545.730            19.690   
171777  PRV51851  PRV54337             1           231.430             1.790   
171778  PRV51908  PRV54337             1           231.430             1.790   

        weight_diagnosis  weight_procedure  
0                  6.000             0.330  
1                  6.000             0.330  
2                 21.500             1.830  
3                 81.220             0.500  
4                  6.500             0.250  
...                  ...               ...  
171774             2.000             0.000  
171775             2.000             0.000  
171776            30.690             0.000  
171777             2.790             0.000  
171778             2.790             0.000  

[171779 rows x 7 columns]